In [4]:
"""
Created by Sumit Kumar on 2020-03-08 && modified by Xisco on 2021-04
Last modified:
"""

import os, sys, numpy, glob, argparse
from datetime import date
import subprocess
from subprocess import call
import re

today = date.today()
date = today.strftime("%Y%m%d")

runname='run_0_mock'
nmax = 0
config_file ='config_n0_to_1_mock.ini'

######
times = '(0 0.2 0.4 0.8 1.2 2 2.5 5 7.5 10 12 15 18 20)'
accounting_group = 'cbc.test.pe_ringdown'
cpus=8
npoints = 2000
req_memory="16GB"
not_user='frjifo@aei.mpg.de'
pythonfile='/work/francisco.jimenez/sio/git/rdstackingproject/code_new/RD_Fits.py'
pythonscript='/work/francisco.jimenez/venv/bin/python'
#######################################################

pwd = os.getcwd()
run_dir = '%s/%s'%(pwd,runname)
logs_dir = '%s/logs'%run_dir

os.system('mkdir -p %s'%logs_dir)
os.system('cp %s %s/'%(config_file,run_dir))

###########################################################################
# Creating Condor submit file
###########################################################################
filename1 = '%s/%s'%(run_dir,'condor_submit')
text_file1 = open(filename1 + ".sub", "w")
text_file1.write("universe   = vanilla\n")
text_file1.write("getenv     = true\n")
text_file1.write("# run script -- make sure that condor has execute permission for this file (chmod a+x script.py)\n")
text_file1.write("executable = "'%s/%s'%(run_dir,runname+'.sh \n'))
text_file1.write("# file to dump stdout (this directory should exist)\n")
text_file1.write("output     = %s/%s-$(Process).out\n"%(logs_dir,runname))
text_file1.write("# file to dump stderr\n")
text_file1.write("error     = %s/%s-$(Process).err\n"%(logs_dir,runname))
text_file1.write("# condor logs\n")
text_file1.write("log     = %s/%s-$(Process).log\n"%(logs_dir,runname))
text_file1.write("initialdir = %s \n"%run_dir)
text_file1.write("notify_user ="+not_user+' \n')
text_file1.write("notification = Complete\n")
text_file1.write('''arguments  = "-processid $(Process)" \n''')
text_file1.write("request_memory = "+str(req_memory)+"\n")
text_file1.write("request_cpus = "+str(cpus)+"\n") 
text_file1.write("on_exit_remove = (ExitBySignal == False) || ((ExitBySignal == True) && (ExitSignal != 11))\n")
text_file1.write("accounting_group = %s\n"%accounting_group)
text_file1.write("queue 1\n")
text_file1.write("\n")
text_file1.close()

###########################################################
# Creating python executable file
############################################################
filename2 = run_dir+'/'+runname+'.sh'
text_file2 = open(filename2, "w") 
text_file2.write("#! /bin/bash \n")
text_file2.write("\n")
text_file2.write("times="+times+"\n")
text_file2.write("config_file="+config_file+"\n")
text_file2.write("pythonfile="+pythonfile+"\n")
text_file2.write("pythonscript="+pythonscript+"\n")
text_file2.write("\n")
text_file2.write("for i in ${times[@]}; do\n")
text_file2.write("   awk -v  a=\"$i\" '/^tshift/ && $3 != \"supplied\" { $3=a } { print }' $config_file > tmp && mv tmp $config_file\n")
text_file2.write("   $pythonscript $pythonfile -c $config_file \n")
text_file2.write("done\n")
text_file2.write("awk -v  a=\"0\" '/^tshift/ && $3 != \"supplied\" { $3=a } { print }' $config_file > tmp && mv tmp $config_file \n")
text_file2.write("\n")
text_file2.close()
os.system('chmod u+x %s'%filename2)

os.system('cp '+runname+'.sh %s/'%run_dir)
os.system('chmod u+x ./'+runname+'.sh')
os.system('cd '+run_dir)

###########################################################
# Checking the configuration file and adding some important replacements
############################################################

filename3 = '%s/%s'%(run_dir,config_file)
# change the number of cores
bashCommand = "awk -v  a="+str(cpus)+" '/^nb_cores/ && $3 != \"supplied\" { $3=a } { print }' "+str(config_file)+" > tmp && mv tmp "+str(config_file);
subprocess.call(bashCommand,shell=True)

filename3 = '%s/%s'%(run_dir,config_file)
# change the number of nmax
bashCommand = "awk -v  a="+str(nmax)+" '/^nmax/ && $3 != \"supplied\" { $3=a } { print }' "+str(config_file)+" > tmp && mv tmp "+str(config_file);
subprocess.call(bashCommand,shell=True)

filename3 = '%s/%s'%(run_dir,config_file)
# change the number of nmax
bashCommand = "awk -v  a="+str(npoints)+" '/^npoints/ && $3 != \"supplied\" { $3=a } { print }' "+str(config_file)+" > tmp && mv tmp "+str(config_file);
subprocess.call(bashCommand,shell=True)

###########################################################
# Submit the job
############################################################
filename4 = '%s/%s'%(run_dir,'condor_submit.sub')
bashCommand = ['condor_submit', str(filename4)]
process = subprocess.Popen(bashCommand, stdout=subprocess.PIPE,stderr=subprocess.PIPE);
output,error = process.communicate()
error

b''